In [ ]:
from glidergun import *

dem1 = grid(".data/n55_e008_1arc_v3.bil")
dem2 = grid(".data/n55_e009_1arc_v3.bil")

dem = mosaic(dem1, dem2)

dem, dem.hillshade(), dem.focal_std().plot("cividis")

"image: 3601x3601 float32 range: -28.000~185.000 mean: 26.346 std: 26.346 crs: EPSG:4326 cell: 0.000555555555555556, 0.000277777777777778Extent(xmin=7.999722222222222, ymin=54.999861111111116, xmax=10.000277777777779, ymax=56.00013888888889)","image: 3601x3601 float32 range: 42.580~253.164 mean: 200.394 std: 200.394 crs: EPSG:4326 cell: 0.000555555555555556, 0.000277777777777778Extent(xmin=7.999722222222222, ymin=54.999861111111116, xmax=10.000277777777779, ymax=56.00013888888889)","image: 3601x3601 float32 range: 0.000~16.632 mean: 0.666 std: 0.666 crs: EPSG:4326 cell: 0.000555555555555556, 0.000277777777777778Extent(xmin=7.999722222222222, ymin=54.999861111111116, xmax=10.000277777777779, ymax=56.00013888888889)"


In [ ]:
dem_resampled = dem.resample(dem.cell_size * 10)

tuple(dem_resampled.focal_mean(n**2).plot("gist_ncar") for n in range(1, 5))

In [ ]:
landsat = stack(
    ".data/LC08_L2SP_197021_20220324_20220330_02_T1_SR_B1.TIF",
    ".data/LC08_L2SP_197021_20220324_20220330_02_T1_SR_B2.TIF",
    ".data/LC08_L2SP_197021_20220324_20220330_02_T1_SR_B3.TIF",
    ".data/LC08_L2SP_197021_20220324_20220330_02_T1_SR_B4.TIF",
    ".data/LC08_L2SP_197021_20220324_20220330_02_T1_SR_B5.TIF",
    ".data/LC08_L2SP_197021_20220324_20220330_02_T1_SR_B6.TIF",
    ".data/LC08_L2SP_197021_20220324_20220330_02_T1_SR_B7.TIF",
).clip(dem.project(32632).extent)

landsat, *landsat.grids

In [ ]:
band5, band4 = landsat.grids[4], landsat.grids[3]

ndvi = (band5 - band4) / (band5 + band4)

ndvi.plot("gist_earth"), (ndvi > 0.3).plot("Greens")

In [ ]:
landsat.plot(4, 3, 2), landsat.plot(5, 7, 6), landsat.plot(1, 7, 5)

In [ ]:
landsat.pca()

image: 1066x931 float32 | crs: EPSG:32632 | cell: 120.0, 120.0 | count: 3 | rgb: (1, 2, 3)

In [ ]:
points = [*(dem_resampled.randomize() < 0.05).set_nan(0, dem_resampled).to_points()]

interp = interp_rbf(points, dem_resampled.crs, dem_resampled.cell_size)

dem_resampled.plot("terrain"), interp.plot("terrain")

"image: 360x360 float32 range: -28.000~169.000 mean: 26.351 std: 26.351 crs: EPSG:4326 cell: 0.00555555555555556, 0.00277777777777778Extent(xmin=7.999722222222222, ymin=55.00013888888889, xmax=9.999722222222225, ymax=56.00013888888889)","image: 359x358 float32 range: -26.925~139.561 mean: 26.338 std: 26.338 crs: EPSG:4326 cell: 0.00555555555555556, 0.00277777777777778Extent(xmin=8.002500000000001, ymin=55.00152777777778, xmax=9.996944444444447, ymax=55.99597222222223)"


In [ ]:
from sklearn.linear_model import Ridge

train_data = landsat.clip((467815, 6190585, 559550, 6273454))

model = train_data.grids[0].fit(Ridge(), *train_data.grids[1:])
model.save(".output/predict_band_1.pickle")

In [ ]:
test_data = landsat.clip((478144, 6104680, 526666, 6148383))

model = load_model(".output/predict_band_1.pickle")
score = model.score(test_data.grids[0], *test_data.grids[1:])
print(f"score: {score}")

actual = test_data.grids[0]
predicted = model.predict(*test_data.grids[1:])

actual.plot("rainbow"), predicted.plot("rainbow")

score: 0.9849321340522815


"image: 404x364 float32 range: 5359.000~14829.000 mean: 8759.100 std: 8759.100 crs: EPSG:32632 cell: 120.0, 120.0Extent(xmin=478144.0, ymin=6104703.0, xmax=526624.0, ymax=6148383.0)","image: 404x364 float32 range: 5304.780~15331.983 mean: 8753.069 std: 8753.069 crs: EPSG:32632 cell: 120.0, 120.0Extent(xmin=478144.0, ymin=6104703.0, xmax=526624.0, ymax=6148383.0)"


In [ ]:
actual.focal_ttest_ind(predicted)

"image: 404x364 float32 range: -4.353~7.167 mean: 0.070 std: 0.070 crs: EPSG:32632 cell: 120.0, 120.0Extent(xmin=478144.0, ymin=6104703.0, xmax=526624.0, ymax=6148383.0)","image: 404x364 float32 range: 0.000~1.000 mean: 0.837 std: 0.837 crs: EPSG:32632 cell: 120.0, 120.0Extent(xmin=478144.0, ymin=6104703.0, xmax=526624.0, ymax=6148383.0)"


In [ ]:
from IPython.display import clear_output

def tick(grid: Grid):
    g = grid.focal_sum() - grid
    return (grid == 1) & (g == 2) | (g == 3)

gosper = landsat.grids[0].resample(3000).randomize() < 0.1
md5s = set()

while gosper.md5 not in md5s:
    md5s.add(gosper.md5)
    display(-(gosper := tick(gosper)))
    clear_output(wait=True)

image: 43x37 int32 | range: -1~0 | mean: -0 | std: -0 | crs: EPSG:32632 | cell: 3000.0, 3000.0